# Test BCN

## Paradas Bus

In [26]:
import pandas as pd
import folium
import matplotlib.pyplot as plt
import re
import random
from folium.plugins import MarkerCluster

In [ ]:
bus_lines = pd.read_csv(".\data\linies_bus.csv")
acc = pd.read_csv('.\data\ccidents_2017.csv')

In [28]:
bus_lines.head()

FID  ID_LINIA  CODI_LINIA NOM_LINIA  \
0  LINIES_BUS.fid-42611e8c_196631efc1c_507f      2999         220       D20   
1  LINIES_BUS.fid-42611e8c_196631efc1c_5080      3025         240       D40   
2  LINIES_BUS.fid-42611e8c_196631efc1c_5081      3051         250       D50   
3  LINIES_BUS.fid-42611e8c_196631efc1c_5082      3068         202        H2   
4  LINIES_BUS.fid-42611e8c_196631efc1c_5083      3018         204        H4   

                        DESC_LINIA        ORIGEN_LINIA       DESTI_LINIA  \
0       Pg. Marítim / Ernest Lluch         Pg. Marítim      Ernest Lluch   
1          Pl. Espanya / Canyelles         Pl. Espanya         Canyelles   
2     Paral·lel / Ciutat Meridiana           Paral·lel  Ciutat Meridiana   
3    Av. Esplugues / Trinitat Nova       Av. Esplugues     Trinitat Nova   
4  Zona Universitària / Bon Pastor  Zona Universitària        Bon Pastor   

   NUM_PAQUETS  ID_OPERADOR  CODI_OPERADOR  ...   NOM_FAMILIA  ORDRE_FAMILIA  \
0            1            2              2  ...     Diagonals             10   
1            1            2              2  ...     Diagonals             10   
2            1            2              2  ...     Diagonals             10   
3            1            2              2  ...  Horitzontals             11   
4            1            2              2  ...  Horitzontals             11   

  ORDRE_LINIA  CODI_TIPUS_CALENDARI  NOM_TIPUS_CALENDARI        DATA  \
0         220                     1        Tots els dies  2025-04-23   
1         240                     1        Tots els dies  2025-04-23   
2         250                     1        Tots els dies  2025-04-23   
3         202                     1        Tots els dies  2025-04-23   
4         204                     1        Tots els dies  2025-04-23   

   COLOR_LINIA  COLOR_AUX_LINIA  COLOR_TEXT_LINIA  \
0       93107E           C987BE            FFFFFF   
1       93107E           C987BE            FFFFFF   
2       93107E           C987BE            FFFFFF   
3       003888           7F9BC3            FFFFFF   
4       003888           7F9BC3            FFFFFF   

                                            GEOMETRY  
0  MULTILINESTRING ((2.1945721433270453 41.385652...  
1  MULTILINESTRING ((2.1497672532744514 41.377435...  
2  MULTILINESTRING ((2.166120553151028 41.3764561...  
3  MULTILINESTRING ((2.1048482603368948 41.385505...  
4  MULTILINESTRING ((2.111158407156105 41.3856839...  

[5 rows x 25 columns]

In [ ]:
def random_color():
    return "#{:06x}".format(random.randint(0, 0xFFFFFF))

# Initialize the map
m_lines = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# Loop through each MULTILINESTRING in your DataFrame
for line in bus_lines['GEOMETRY']:
    # Extract coordinates
    pattern = re.findall(r"[-+]?[0-9]*\.?[0-9]+", line)
    coords = list(map(float, pattern))
    points = [(coords[i+1], coords[i]) for i in range(0, len(coords), 2)]

    if not points:
        continue

    # Generate a unique color for this line
    line_color = random_color()

    # Add the bus line to the map
    folium.PolyLine(points, color='blue', weight=1).add_to(m_lines)

    # Add circle markers at each bus stop
    #for lat, lon in points:
    #    folium.CircleMarker(
    #        location=(lat, lon),
    #        radius=2,
    #        color=line_color,
    #        fill=True,
    #        fill_color=line_color,
    #        fill_opacity=0.9
    #    ).add_to(m_lines)



marker_cluster = MarkerCluster().add_to(m_lines)

for _, row in acc.iterrows():
    folium.CircleMarker(
        location=[row["Latitude"], row["Longitude"]],
        radius=0.1,
        color="red",
        fill=True,
        fill_color="red",
        fill_opacity=0.9
    ).add_to(marker_cluster)

# Display the map
m_lines

In [ ]:
# Cargar datos
bus_stops = pd.read_csv('data/bus_stops.csv')

# Crear mapa centrado en Barcelona
m = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# Colores únicos por distrito
districts = bus_stops['District.Name'].unique()
colors = plt.cm.get_cmap('tab10', len(districts))
district_color_map = {
    district: f"#{int(colors(i)[0]*255):02x}{int(colors(i)[1]*255):02x}{int(colors(i)[2]*255):02x}"
    for i, district in enumerate(districts)
}

# Añadir paradas al mapa, agrupadas por distrito
for district in districts:
    color = district_color_map[district]
    group = folium.FeatureGroup(name=district)

    stops_district = bus_stops[bus_stops['District.Name'] == district]
    for _, row in stops_district.iterrows():
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=4,
            popup=f"{row['Neighborhood.Name']}<br>{row['District.Name']}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7
        ).add_to(group)

    group.add_to(m)

# Añadir control de capas (toggle distritos)
folium.LayerControl(collapsed=False).add_to(m)

# Guardar el mapa
#m.save('mapa_barcelona_featuregroup.html')
m

FileNotFoundError: [Errno 2] No such file or directory: 'data/bus_stops.csv'

In [ ]:
import pandas as pd
import folium
import matplotlib.pyplot as plt

# Cargar datos
bus_stops = pd.read_csv('data/bus_stops.csv')
transports = pd.read_csv('data/transports.csv')

# Crear mapa base
m = folium.Map(location=[41.3851, 2.1734], zoom_start=12, tiles="CartoDB positron")

# -----------------------------
# PARADAS DE BUS por distrito
# -----------------------------
districts = bus_stops['District.Name'].unique()
colors = plt.cm.get_cmap('tab10', len(districts))
district_color_map = {
    district: f"#{int(colors(i)[0]*255):02x}{int(colors(i)[1]*255):02x}{int(colors(i)[2]*255):02x}"
    for i, district in enumerate(districts)
}

for district in districts:
    color = district_color_map[district]
    group = folium.FeatureGroup(name=f"🚌 Bus - {district}")

    stops_district = bus_stops[bus_stops['District.Name'] == district]
    for _, row in stops_district.iterrows():
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=4,
            popup=f"{row['Neighborhood.Name']}<br>{row['District.Name']}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.7
        ).add_to(group)

    group.add_to(m)

# -----------------------------
# TRANSPORTES por tipo (Underground, Tram, etc.)
# -----------------------------
transport_types = transports['Transport'].dropna().unique()
transport_colors = plt.cm.get_cmap('Set1', len(transport_types))
type_color_map = {
    t: f"#{int(transport_colors(i)[0]*255):02x}{int(transport_colors(i)[1]*255):02x}{int(transport_colors(i)[2]*255):02x}"
    for i, t in enumerate(transport_types)
}

for transport_type in transport_types:
    color = type_color_map[transport_type]
    group = folium.FeatureGroup(name=f"🚉 {transport_type}")

    stops = transports[transports['Transport'] == transport_type]
    for _, row in stops.iterrows():
        if pd.isna(row['Latitude']) or pd.isna(row['Longitude']):
            continue
        folium.CircleMarker(
            location=[row['Latitude'], row['Longitude']],
            radius=6,
            popup=f"{row['Station']}<br>{row['District.Name'] or ''}",
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.9
        ).add_to(group)

    group.add_to(m)

# -----------------------------
# Control de capas
# -----------------------------
folium.LayerControl(collapsed=False).add_to(m)

# Guardar
m.save('mapa_barcelona_bus_transportes.html')


/var/folders/dh/_ks73kfn57l67vxm7b5y16qw0000gn/T/ipykernel_39847/3759938902.py:16: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  colors = plt.cm.get_cmap('tab10', len(districts))
/var/folders/dh/_ks73kfn57l67vxm7b5y16qw0000gn/T/ipykernel_39847/3759938902.py:44: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  transport_colors = plt.cm.get_cmap('Set1', len(transport_types))
